# Task1: Data format changing

## import and initializing of S3

In [9]:
import boto3
import pandas as pd
import re
import io
import numpy as np
import seaborn as sns
import matplotlib.pyplot as plt

from datetime import datetime # for timestamp to day
import pytz # for timestamp to day

In [10]:
s3 = boto3.client('s3')
bucket_name = 'young-elevator-data'

## Get data from S3 raw-data and restore to format-changed-data

In [11]:
def parse_value(data):
    match = re.search(r'value=([\d\.-]+)', data)
    return float(match.group(1)) if match else None

def parse_timestamp(data):
    match = re.search(r'timestamp=(\d+)', data)
    return int(match.group(1)) if match else None

def parse_gpid(data):
    match = re.search(r'gpid=(\w+)', data)
    return match.group(1) if match else None

def parse_geid(data):
    match = re.search(r'geid=(\w+)', data)
    return match.group(1) if match else None

def convert_to_eastern(timestamp_ms):
    timestamp_sec = timestamp_ms / 1000.0
    dt_utc = datetime.utcfromtimestamp(timestamp_sec)
    dt_eastern = dt_utc.replace(tzinfo=pytz.utc).astimezone(pytz.timezone('America/New_York'))
    return dt_eastern

In [12]:
def process_file(file_key, file_type):
    response = s3.get_object(Bucket=bucket_name, Key=file_key)
    lines = response['Body'].read().decode('utf-8').splitlines()

    if not lines:
        print(f"Skipping empty file: {file_key}")
        return
        
    df = pd.read_csv(io.StringIO("\n".join(lines)))
    
    df['timestamp'] = df['var_1'].apply(parse_timestamp)
    df['val_1'] = df['var_1'].apply(parse_value)
    df['accel_x_axis_g'] = df['accel_x_axis_g'].apply(parse_value)
    df['accel_y_axis_g'] = df['accel_y_axis_g'].apply(parse_value)
    df['accel_z_axis_g'] = df['accel_z_axis_g'].apply(parse_value)
    df['door_state'] = df['door_state'].apply(parse_value)
    df['PID'] = df['id'].apply(parse_gpid)
    df['EID'] = df['id'].apply(parse_geid)

    df['day'] = df['timestamp'].apply(lambda x: convert_to_eastern(x).date()) # get day
    
    df = df[['timestamp', 'val_1', 'accel_x_axis_g', 'accel_y_axis_g', 'accel_z_axis_g', 'door_state', 'PID', 'EID', 'day']]
    
    new_file_name = f"format-changed-data/{file_type}.csv"
    csv_buffer = io.StringIO()
    df.to_csv(csv_buffer, index=False)
    s3.put_object(Bucket=bucket_name, Body=csv_buffer.getvalue(), Key=new_file_name)
    print(f"Processed and saved: {new_file_name}")

# Process train.csv and test.csv files

In [13]:
process_file("raw-data/train.csv", "train")
process_file("raw-data/test.csv", "test")

Processed and saved: format-changed-data/train.csv
Processed and saved: format-changed-data/test.csv


## read the train csv file 

In [14]:
s3_path_train = f"s3://{bucket_name}/format-changed-data/train.csv"
train_df = pd.read_csv(s3_path_train)

# TASK #2: VISUALIZE DATASET

In [67]:
# 연속된 행에서 door_state가 모두 1인 경우를 체크하기 위한 조건 설정
group_condition = (train_df['door_state'] == 1) & (train_df['door_state'].shift(1) == 1) & (train_df['timestamp'].diff().fillna(10001) < 10000)

In [73]:
print(group_condition.head(60))

0     False
1      True
2     False
3     False
4     False
5     False
6     False
7     False
8     False
9     False
10    False
11    False
12    False
13    False
14    False
15    False
16    False
17    False
18    False
19    False
20    False
21    False
22    False
23    False
24    False
25    False
26    False
27    False
28    False
29     True
30     True
31     True
32     True
33     True
34     True
35     True
36     True
37     True
38     True
39     True
40     True
41     True
42     True
43     True
44     True
45     True
46     True
47     True
48     True
49     True
50     True
51     True
52     True
53     True
54     True
55     True
56     True
57     True
58     True
59     True
dtype: bool


In [82]:
group_number = 0   # 현재 그룹 번호
current_group = False  # 현재 그룹의 상태를 추적하는 플래그
group_numbers = []  # 각 데이터 포인트의 그룹 번호를 저장할 리스트

for condition in group_condition:
    if condition:
        if not current_group:
            # 새로운 True 그룹이 시작됨
            group_number += 1
            current_group = True
    else:
        current_group = False

    # 현재 그룹 번호를 리스트에 추가
    group_numbers.append(group_number if condition else 0)

# group_numbers 리스트를 데이터프레임에 추가
train_df['group'] = group_numbers
print(train_df['group'].head(60))

0     0
1     1
2     0
3     0
4     0
5     0
6     0
7     0
8     0
9     0
10    0
11    0
12    0
13    0
14    0
15    0
16    0
17    0
18    0
19    0
20    0
21    0
22    0
23    0
24    0
25    0
26    0
27    0
28    0
29    2
30    2
31    2
32    2
33    2
34    2
35    2
36    2
37    2
38    2
39    2
40    2
41    2
42    2
43    2
44    2
45    2
46    2
47    2
48    2
49    2
50    2
51    2
52    2
53    2
54    2
55    2
56    2
57    2
58    2
59    2
Name: group, dtype: int64


In [84]:
grouped = train_df.groupby('group')
for name, group in grouped:
    if group['door_state'].iloc[0] == 1:
        start_time = group['timestamp'].iloc[0]
        end_time = group['timestamp'].iloc[-1]
        start_val = group['val_1'].iloc[0]
        end_val = group['val_1'].iloc[-1]
        direction = 'Down' if end_val > start_val else 'Up'
        move_time = end_time - start_time
        move_distance = abs(end_val - start_val)
        print(f'Group {name}: Direction: {direction}, Move Time: {start_time, end_time, move_time}, Move Distance: {move_distance}')

Group 0: Direction: Down, Move Time: (1675685889003, 1675988828035, 302939032), Move Distance: 3.42529296875
Group 1: Direction: Up, Move Time: (1675685889501, 1675685889501, 0), Move Distance: 0.0
Group 2: Direction: Up, Move Time: (1675685905264, 1675685934033, 28769), Move Distance: 2.81591796875
Group 3: Direction: Down, Move Time: (1675687216452, 1675687244085, 27633), Move Distance: 2.12646484375
Group 4: Direction: Down, Move Time: (1675687260169, 1675687268273, 8104), Move Distance: 0.3837890625
Group 5: Direction: Up, Move Time: (1675687283995, 1675687289511, 5516), Move Distance: 0.344970703125
Group 6: Direction: Down, Move Time: (1675687507324, 1675687514363, 7039), Move Distance: 0.38037109375
Group 7: Direction: Up, Move Time: (1675687530521, 1675687537624, 7103), Move Distance: 0.3701171875
Group 8: Direction: Down, Move Time: (1675687864703, 1675687871600, 6897), Move Distance: 0.411865234375
Group 9: Direction: Up, Move Time: (1675687889815, 1675687893861, 4046), Move 

In [59]:
plt.figure(figsize=(120, 6))
for name, group in grouped:
    if group['door_state'].iloc[0] == 1:
        plt.plot(group['timestamp'], group['val_1'], marker='o', label=f'Group {name}')
plt.xlabel('Timestamp')
plt.ylabel('val_1')
plt.title('Elevator Movement Analysis')
plt.legend()
plt.show()